<a href="https://colab.research.google.com/github/oskargirardin/CRP_GDPR_datasets/blob/master/CTGAN_tests_Oskar.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# 0. SETUP

In [ ]:
! pip install ctgan --quiet
! pip install table_evaluator --quiet
! pip install kaggle --quiet
! pip install seaborn --quiet
! pip install sdmetrics --quiet

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 40.8/40.8 KB 2.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 63.6/63.6 KB 3.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.7/1.7 MB 43.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 280.2/280.2 KB 12.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 285.0/285.0 KB 27.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.2/12.2 MB 36.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 17.3/17.3 MB 86.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 140.2/140.2 KB 8.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 15.2/15.2 MB 42.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 53.6/53.6 KB 5.9 MB/s eta 0:00:00


In [ ]:
! mkdir ~/.kaggle

! cp kaggle.json ~/.kaggle/

! chmod 600 ~/.kaggle/kaggle.json

!kaggle datasets download -d subhamjain/loan-prediction-based-on-customer-behavior

!unzip loan-prediction-based-on-customer-behavior.zip

 97% 5.00M/5.15M [00:01<00:00, 4.64MB/s]
100% 5.15M/5.15M [00:01<00:00, 3.00MB/s]
Archive:  loan-prediction-based-on-customer-behavior.zip
  inflating: Sample Prediction Dataset.csv  
  inflating: Test Data.csv           
  inflating: Training Data.csv       


In [ ]:
from ctgan import CTGAN
import pandas as pd

# 1. Retrieve the data

In [ ]:
data = pd.read_csv("Training Data.csv")
data = data.drop("Id", axis = 1)

In [ ]:
data

# 2. Fit the model & Generate synthetic data

In [ ]:
ctgan = CTGAN(verbose=True)

discrete_columns = data.columns[1:]
ctgan.fit(data, discrete_columns, epochs=10)

Epoch 1, Loss G:  0.8776,Loss D: -0.0574
Epoch 2, Loss G: -0.2080,Loss D: -0.0471
Epoch 3, Loss G: -1.0610,Loss D:  0.0870
Epoch 4, Loss G: -1.4982,Loss D:  0.0568
Epoch 5, Loss G: -1.6357,Loss D:  0.0199
Epoch 6, Loss G: -1.7323,Loss D: -0.0161
Epoch 7, Loss G: -1.6926,Loss D:  0.0458
Epoch 8, Loss G: -1.7330,Loss D:  0.0153
Epoch 9, Loss G: -1.9268,Loss D: -0.0740
Epoch 10, Loss G: -1.8405,Loss D: -0.0926


In [7]:
sample = ctgan.sample(len(data))

# 3. Evaluate similarity between datasets

In [ ]:
from sdmetrics import load_demo
from sdmetrics.reports.single_table import QualityReport

real_data, synthetic_data, metadata = load_demo(modality='single_table')

my_report = QualityReport()
my_report.generate(real_data, synthetic_data, metadata)

Creating report: 100%|██████████| 4/4 [00:01<00:00,  3.53it/s]



Overall Quality Score: 81.44%

Properties:
Column Shapes: 81.56%
Column Pair Trends: 81.33%


In [ ]:
my_metadata = {
  'fields': 
    {
    'Income': {'type': 'numerical', 'subtype': 'integer'},
    'Age': {'type': 'numerical', 'subtype': 'integer'},
    'Experience': {'type': 'numerical', 'subtype': 'integer'},
    'CURRENT_JOB_YRS': {'type': 'numerical', 'subtype': 'integer'},
    'CURRENT_HOUSE_YRS': {'type': 'numerical', 'subtype': 'integer'},
    'Married/Single': {'type': 'categorical'},
    'House_Ownership': {'type': 'categorical'},
    'Car_Ownership': {'type': 'categorical'},
    'Profession': {'type': 'categorical'},
    'CITY': {'type': 'categorical'},
    'STATE': {'type': 'categorical'},
    'Risk_Flag': {'type': 'boolean'}
  },
  'constraints': [],
  'model_kwargs': {},
  'name': None,
  'primary_key': None,
  'sequence_index': None,
  'entity_columns': [],
  'context_columns': []
}

In [ ]:
report = QualityReport()
report.generate(data, sample, my_metadata)

Creating report: 100%|██████████| 4/4 [00:03<00:00,  1.03it/s]



Overall Quality Score: 81.43%

Properties:
Column Shapes: 88.22%
Column Pair Trends: 74.64%


## 3.1 Single columns

In [ ]:
report.get_details(property_name='Column Shapes')

Column        Metric  Quality Score
0              Income  KSComplement       0.873786
1                 Age  KSComplement       0.921556
2          Experience  KSComplement       0.935639
3     CURRENT_JOB_YRS  KSComplement       0.911861
4   CURRENT_HOUSE_YRS  KSComplement       0.777004
5      Married/Single  TVComplement       0.964905
6     House_Ownership  TVComplement       0.965508
7       Car_Ownership  TVComplement       0.982587
8          Profession  TVComplement       0.780702
9                CITY  TVComplement       0.706036
10              STATE  TVComplement       0.815012
11          Risk_Flag  TVComplement       0.952000

In [ ]:
from sdmetrics.reports.utils import get_column_plot
get_column_plot(
    real_data=data,
    synthetic_data=sample,
    metadata=my_metadata,
    column_name="Age"
)

In [ ]:
get_column_plot(
    real_data=data,
    synthetic_data=sample,
    metadata=my_metadata,
    column_name="Experience"
)

In [ ]:
get_column_plot(
    real_data=data,
    synthetic_data=sample,
    metadata=my_metadata,
    column_name="Married/Single"
)

In [ ]:
get_column_plot(
    real_data=data,
    synthetic_data=sample,
    metadata=my_metadata,
    column_name="Profession"
)

## 3.2 Column pairs

In [ ]:
report.get_visualization(property_name='Column Pair Trends')

# 4. Compare model performance on both datasets

In [31]:
import sklearn
from sklearn.preprocessing import OneHotEncoder
from sklearn.linear_model import LinearRegression

In [46]:
useless_columns = ["CITY", "STATE"]
n_train = 100000
n_test = 10000
synth = sample.drop(useless_columns, axis = 1)[:n_train]
real = data.drop(useless_columns, axis = 1)[:n_train]
test = data.drop(useless_columns, axis = 1)[n_train:(n_train+n_test)]

In [47]:
cat_cols = ["Profession", "Married/Single", "House_Ownership", "Car_Ownership"]
for df in [synth, real, test]:
  for col in cat_cols:
    onehot = OneHotEncoder()
    ohe_matrix = onehot.fit_transform(df[[col]])
    df[onehot.categories_[0]] = ohe_matrix.toarray()

In [48]:
for df in [synth, real, test]:
  df.drop(cat_cols, axis = 1, inplace = True)

In [50]:
ols_real = LinearRegression()
y = real[["Income"]].to_numpy()
X = real.drop(["Income", "no"], axis = 1).to_numpy()
ols_real.fit(X, y)

In [53]:
ols_synth = LinearRegression()
y = synth[["Income"]].to_numpy()
X = synth.drop(["Income", "no"], axis = 1).to_numpy()
ols_synth.fit(X, y)

LinearRegression()

In [54]:
y_test = test[["Income"]].to_numpy()
X_test = test.drop(["Income", "no"], axis = 1).to_numpy()

In [61]:
ols_synth.score(X_test, y_test)

-0.0007964936486202223

In [59]:
def evaluate_model(fitted_model, X_test, y_test):
  score = fitted_model.score(X_test, y_test)
  return score

def compare_real_synth(fitted_model_real, fitted_model_synth, X_test, y_test):
  score_real = evaluate_model(fitted_model_real, X_test, y_test)
  score_synth = evaluate_model(fitted_model_synth, X_test, y_test)
  print(f"Score on real dataset: {score_real}\nScore on synthetic dataset: {score_synth}")

In [60]:
compare_real_synth(ols_real, ols_synth, X_test, y_test)

Score on real dataset: 0.0063145378001785435
Score on synthetic dataset: -0.0007964936486202223
